In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
%matplotlib inline

In [3]:
df = pd.read_csv("../datasets/train_radiomics_hipocamp.csv")


X_test = pd.read_csv("../datasets/test_radiomics_hipocamp.csv")

In [4]:
# Verificar os tipos de dados únicos
unique_dtypes = df.dtypes.unique()
print("Tipos de dados únicos:", unique_dtypes)


Tipos de dados únicos: [dtype('O') dtype('int64') dtype('float64')]


In [5]:
df_num = df.select_dtypes(exclude=[object])
df_num.columns
df_num.head()

diagnostics_Image-original_Dimensionality  diagnostics_Image-original_Mean  \
0                                          3                         5.848123   
1                                          3                         5.238834   
2                                          3                         6.816667   
3                                          3                         6.445162   
4                                          3                         5.568269   

   diagnostics_Image-original_Minimum  diagnostics_Image-original_Maximum  \
0                                   0                                 178   
1                                   0                                 190   
2                                   0                                 155   
3                                   0                                 171   
4                                   0                                 150   

   diagnostics_Mask-original_VoxelNum  diagnostics_Mask-original_VolumeNum  \
0                                7106                                    2   
1                                7779                                    2   
2                                6707                                    2   
3                                8281                                    2   
4                                5986                                    2   

   original_shape_Elongation  original_shape_Flatness  \
0                   0.420040                 0.106547   
1                   0.425482                 0.102532   
2                   0.447685                 0.135582   
3                   0.418896                 0.099626   
4                   0.411851                 0.080719   

   original_shape_LeastAxisLength  original_shape_MajorAxisLength  ...  \
0                       10.757474                      100.964915  ...   
1                       10.432362                      101.747321  ...   
2                       14.370911                      105.993915  ...   
3                       10.639815                      106.797600  ...   
4                        8.885188                      110.075144  ...   

   lbp-3D-k_glszm_ZoneEntropy  lbp-3D-k_glszm_ZonePercentage  \
0                    3.021791                       0.007881   
1                    2.533247                       0.013112   
2                    2.718587                       0.011331   
3                    2.603621                       0.012197   
4                    3.073515                       0.010859   

   lbp-3D-k_glszm_ZoneVariance  lbp-3D-k_ngtdm_Busyness  \
0                345733.167092               479.414935   
1                244310.331892               378.001763   
2                222776.529605               497.261162   
3                280222.663268               406.837667   
4                216779.591479               368.838125   

   lbp-3D-k_ngtdm_Coarseness  lbp-3D-k_ngtdm_Complexity  \
0                   0.001538                   0.183049   
1                   0.001761                   0.146021   
2                   0.001567                   0.190309   
3                   0.001629                   0.148247   
4                   0.001912                   0.174701   

   lbp-3D-k_ngtdm_Contrast  lbp-3D-k_ngtdm_Strength  Sex   Age  
0                 0.017044                 0.001581    0  77.1  
1                 0.010782                 0.001813    1  83.4  
2                 0.019644                 0.001596    1  81.3  
3                 0.010824                 0.001677    1  79.6  
4                 0.014793                 0.001979    0  80.1  

[5 rows x 2161 columns]

In [ ]:
print(list(df.columns))

In [ ]:
# Verificar se há colunas com nomes duplicados
duplicated_columns = df.columns[df.columns.duplicated()]
print("Colunas com o mesmo nome:", duplicated_columns)


In [ ]:
colunas_unicas = df.columns[df.nunique() == 1]

print("Colunas com um único valor único:")
print(colunas_unicas)

# Remover valores nao numericos

In [3]:
X = df.drop(['Transition'], axis=1)     
y = df['Transition'].to_frame()  

In [4]:
X_numerico = X.select_dtypes(include=[np.number])

X_test = X_test.select_dtypes(include=[np.number])
X_numerico.columns.value_counts()

diagnostics_Image-original_Dimensionality             1
squareroot_glcm_ClusterTendency                       1
squareroot_glcm_JointEnergy                           1
squareroot_glcm_JointAverage                          1
squareroot_glcm_InverseVariance                       1
                                                     ..
wavelet-HHH_gldm_DependenceNonUniformityNormalized    1
wavelet-HHH_gldm_DependenceNonUniformity              1
wavelet-HHH_gldm_DependenceEntropy                    1
wavelet-HHH_glcm_SumSquares                           1
Age                                                   1
Name: count, Length: 2161, dtype: int64

# Transformar Classe em numerico

In [17]:
df['Transition'] = df['Transition'].map({
    'CN-CN': 0,
    'CN-MCI': 1,
    'MCI-MCI': 2,
    'MCI-AD': 3,
    'AD-AD': 4
})

# MinMaxScaler

In [5]:
from sklearn.preprocessing import StandardScaler,MinMaxScaler
scaler = MinMaxScaler()
X_numerico = pd.DataFrame(scaler.fit_transform(X_numerico), columns=X_numerico.columns, index=X_numerico.index) #normalização

X_test = pd.DataFrame(scaler.fit_transform(X_test), columns=X_test.columns, index=X_test.index)

# RFE com LR top 10% features

In [13]:
from sklearn.feature_selection import RFE
from sklearn.linear_model import LogisticRegression

# Treinar um modelo para o RFE
model = LogisticRegression(random_state=2022, solver='newton-cg')
rfe = RFE(model, n_features_to_select=220)  # Seleciona as 220 melhores features
X_train_rfe = rfe.fit_transform(X_numerico, y)

# Obter as features selecionadas
selected_features = X_numerico.columns[rfe.support_]
print("Features selecionadas:", selected_features)


c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expec

Features selecionadas: Index(['diagnostics_Image-original_Mean', 'original_shape_Elongation',
       'original_shape_Maximum2DDiameterSlice', 'original_firstorder_Kurtosis',
       'original_glcm_Idmn', 'original_glcm_MaximumProbability',
       'original_glrlm_HighGrayLevelRunEmphasis',
       'original_glszm_GrayLevelNonUniformityNormalized',
       'original_glszm_HighGrayLevelZoneEmphasis',
       'original_glszm_SizeZoneNonUniformity',
       ...
       'lbp-3D-k_gldm_SmallDependenceEmphasis',
       'lbp-3D-k_gldm_SmallDependenceHighGrayLevelEmphasis',
       'lbp-3D-k_glszm_GrayLevelNonUniformity',
       'lbp-3D-k_glszm_SizeZoneNonUniformityNormalized',
       'lbp-3D-k_glszm_SmallAreaEmphasis',
       'lbp-3D-k_glszm_SmallAreaLowGrayLevelEmphasis',
       'lbp-3D-k_glszm_ZoneEntropy', 'lbp-3D-k_glszm_ZonePercentage', 'Sex',
       'Age'],
      dtype='object', length=220)


c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [19]:
X_numerico_features = X_numerico[selected_features]
X_test = X_test[selected_features]

log = LogisticRegression(random_state=2022, solver='newton-cg')
log.fit(X_numerico_features, y)


c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


LogisticRegression(random_state=2022, solver='newton-cg')

In [21]:
predictions = log.predict(X_test)
predictions

array(['MCI-AD', 'MCI-MCI', 'AD-AD', 'CN-CN', 'CN-CN', 'MCI-AD', 'MCI-AD',
       'CN-CN', 'AD-AD', 'MCI-MCI', 'MCI-AD', 'MCI-AD', 'MCI-AD',
       'MCI-AD', 'AD-AD', 'MCI-MCI', 'MCI-AD', 'AD-AD', 'AD-AD', 'AD-AD',
       'CN-CN', 'MCI-AD', 'CN-CN', 'CN-CN', 'AD-AD', 'CN-CN', 'AD-AD',
       'AD-AD', 'CN-MCI', 'MCI-MCI', 'CN-CN', 'MCI-MCI', 'MCI-AD',
       'AD-AD', 'MCI-MCI', 'MCI-AD', 'MCI-AD', 'CN-CN', 'MCI-MCI',
       'MCI-MCI', 'MCI-AD', 'CN-CN', 'AD-AD', 'CN-MCI', 'CN-CN', 'AD-AD',
       'MCI-MCI', 'CN-CN', 'AD-AD', 'MCI-MCI', 'MCI-MCI', 'MCI-MCI',
       'AD-AD', 'MCI-AD', 'MCI-MCI', 'AD-AD', 'CN-CN', 'CN-CN', 'AD-AD',
       'CN-CN', 'CN-CN', 'MCI-AD', 'MCI-MCI', 'AD-AD', 'MCI-AD', 'AD-AD',
       'MCI-AD', 'MCI-AD', 'AD-AD', 'MCI-MCI', 'CN-CN', 'MCI-AD', 'CN-CN',
       'AD-AD', 'MCI-AD', 'AD-AD', 'MCI-MCI', 'MCI-AD', 'MCI-MCI',
       'CN-CN', 'CN-MCI', 'MCI-AD', 'AD-AD', 'CN-CN', 'AD-AD', 'AD-AD',
       'AD-AD', 'MCI-AD', 'CN-CN', 'CN-CN', 'MCI-MCI', 'MCI-MCI',
       'MC

In [6]:
from sklearn.preprocessing import StandardScaler,MinMaxScaler
scaler = StandardScaler()
X_numerico = scaler.fit_transform(X_numerico)
X_test = scaler.transform(X_test)

# RFE com melhor resultados de features entre 100 e 1200

In [20]:
from sklearn.model_selection import cross_val_score
import numpy as np



# Função para avaliar o modelo com RFE e número variável de features
def evaluate_rfe(num_features):
    model = LogisticRegression(random_state=2022, solver='newton-cg')
    rfe = RFE(estimator=model, n_features_to_select=num_features)
    X_train_rfe = rfe.fit_transform(X_numerico, y)
    score = np.mean(cross_val_score(model, X_train_rfe, y, cv=5))  # Usando 5-fold cross-validation
    return score

# Testar diferentes números de features (por exemplo: de 100 a 1000)
scores = []
for num_features in range(100, 1001, 100):  # Tentar de 100 em 100 features
    score = evaluate_rfe(num_features)
    scores.append((num_features, score))

# Imprimir resultados
for num_features, score in scores:
    print(f"Features: {num_features}, Score: {score}")


c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expec

Features: 100, Score: 0.5672131147540984
Features: 200, Score: 0.5540983606557377
Features: 300, Score: 0.5344262295081966
Features: 400, Score: 0.5147540983606558
Features: 500, Score: 0.48196721311475405
Features: 600, Score: 0.4688524590163935
Features: 700, Score: 0.4590163934426229
Features: 800, Score: 0.44918032786885237
Features: 900, Score: 0.44590163934426225
Features: 1000, Score: 0.439344262295082


c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [27]:
# Selecionar as features finais
best_num_features = 100  # Substitua pelo número ideal encontrado


from sklearn.feature_selection import RFE
from sklearn.linear_model import LogisticRegression

# Treinar um modelo para o RFE
model = LogisticRegression(random_state=2022, solver='newton-cg')
rfe = RFE(model, n_features_to_select=best_num_features)  # Seleciona as 220 melhores features
X_train_rfe = rfe.fit_transform(X_numerico, y)

# Obter as features selecionadas
selected_features = X_numerico.columns[rfe.support_]
print("Features selecionadas:", selected_features)

c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expec

Features selecionadas: Index(['diagnostics_Image-original_Mean',
       'original_shape_Maximum2DDiameterSlice', 'original_firstorder_Kurtosis',
       'original_glcm_MaximumProbability',
       'original_glszm_HighGrayLevelZoneEmphasis',
       'original_glszm_SizeZoneNonUniformity',
       'original_glszm_SmallAreaEmphasis', 'wavelet-LLH_firstorder_Skewness',
       'wavelet-LLH_glcm_ClusterShade', 'wavelet-LLH_gldm_DependenceEntropy',
       'wavelet-LLH_gldm_LargeDependenceLowGrayLevelEmphasis',
       'wavelet-LLH_glrlm_GrayLevelNonUniformityNormalized',
       'wavelet-LLH_glszm_SizeZoneNonUniformityNormalized',
       'wavelet-LLH_glszm_SmallAreaEmphasis',
       'wavelet-LLH_glszm_SmallAreaHighGrayLevelEmphasis',
       'wavelet-LLH_glszm_SmallAreaLowGrayLevelEmphasis',
       'wavelet-LLH_ngtdm_Contrast',
       'wavelet-LHL_gldm_DependenceNonUniformityNormalized',
       'wavelet-LHL_glszm_SmallAreaEmphasis',
       'wavelet-LHH_firstorder_Skewness', 'wavelet-LHH_glcm_JointEn

c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expec

In [28]:
X_numerico_features = X_numerico[selected_features]
X_test = X_test[selected_features]

log = LogisticRegression(random_state=2022, solver='newton-cg')
log.fit(X_numerico_features, y)

c:\Users\talex\miniconda3\envs\myenv\Lib\site-packages\sklearn\utils\validation.py:1339: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


LogisticRegression(random_state=2022, solver='newton-cg')

In [29]:
predictions = log.predict(X_test)
predictions

array(['AD-AD', 'MCI-AD', 'MCI-MCI', 'CN-CN', 'CN-CN', 'MCI-AD', 'MCI-AD',
       'CN-CN', 'AD-AD', 'AD-AD', 'MCI-AD', 'MCI-AD', 'MCI-AD', 'MCI-AD',
       'AD-AD', 'MCI-MCI', 'CN-CN', 'AD-AD', 'AD-AD', 'AD-AD', 'CN-CN',
       'CN-CN', 'CN-CN', 'CN-CN', 'AD-AD', 'CN-CN', 'AD-AD', 'AD-AD',
       'AD-AD', 'MCI-MCI', 'CN-CN', 'MCI-MCI', 'MCI-AD', 'AD-AD',
       'MCI-MCI', 'MCI-AD', 'AD-AD', 'MCI-MCI', 'CN-CN', 'CN-CN',
       'MCI-AD', 'CN-CN', 'AD-AD', 'CN-CN', 'CN-CN', 'AD-AD', 'CN-CN',
       'CN-CN', 'AD-AD', 'MCI-MCI', 'MCI-MCI', 'MCI-AD', 'AD-AD', 'AD-AD',
       'CN-CN', 'AD-AD', 'CN-CN', 'CN-CN', 'AD-AD', 'CN-CN', 'CN-CN',
       'MCI-AD', 'CN-CN', 'AD-AD', 'AD-AD', 'CN-CN', 'MCI-AD', 'MCI-AD',
       'AD-AD', 'CN-CN', 'CN-CN', 'MCI-AD', 'CN-CN', 'MCI-AD', 'AD-AD',
       'AD-AD', 'AD-AD', 'MCI-AD', 'MCI-MCI', 'CN-CN', 'CN-CN', 'MCI-AD',
       'AD-AD', 'CN-CN', 'AD-AD', 'AD-AD', 'AD-AD', 'MCI-MCI', 'CN-CN',
       'CN-CN', 'MCI-MCI', 'MCI-MCI', 'MCI-MCI', 'MCI-AD', 'MCI-MCI',


# XG_Boost

In [ ]:
xgb_model = xgb.XGBClassifier(objective='binary:logistic', eval_metric='logloss', use_label_encoder=False, random_state=2022)
xgb_model.fit(X_numerico, y)

In [ ]:
import matplotlib.pyplot as plt

# Plotar a importância das características
xgb.plot_importance(xgb_model, importance_type='weight')
plt.show()

# XG_BOOST com GRID_SEARCH

In [24]:
from sklearn.model_selection import GridSearchCV

# Definir o grid de hiperparâmetros
param_grid = {
    'max_depth': [3, 5, 7],
    'learning_rate': [0.01, 0.1, 0.2],
    'n_estimators': [100, 200],
    'subsample': [0.8, 1.0],
    'colsample_bytree': [0.8, 1.0]
}

In [ ]:
grid_search = GridSearchCV(estimator=xgb.XGBClassifier(objective='binary:logistic', random_state=2022),
                           param_grid=param_grid,
                           scoring='accuracy',
                           cv=3,  # Validação cruzada com 3 dobras
                           verbose=1)

# Ajustar o modelo com GridSearch
grid_search.fit(X_numerico, y)

In [ ]:
print("Melhores Hiperparâmetros:", grid_search.best_params_)

Melhores Hiperametros

In [39]:
# Melhores parâmetros obtidos do GridSearchCV
best_params = {
    'colsample_bytree': 0.8,
    'learning_rate': 0.1,
    'max_depth': 5,
    'n_estimators': 200,
    'subsample': 0.8
}

# Parâmetros adicionais que você definiu
additional_params = {
    'objective': 'binary:logistic',  # Tipo de objetivo binário
    'eval_metric': 'logloss',  # Métrica de avaliação
    'use_label_encoder': False,  # Para evitar warning relacionado ao label encoder
    'random_state': 2022  # Definir a semente para reprodutibilidade
}

In [ ]:
xgb_model = xgb.XGBClassifier(**best_params, **additional_params)
xgb_model.fit(X_numerico, y)

In [ ]:
import matplotlib.pyplot as plt

xgb.plot_importance(xgb_model, importance_type='weight', max_num_features=20)
plt.show()


# Predicts

In [1]:
predictions = xgb_model.predict(X_test)
predictions = [round(pred) for pred in predictions]

reverse_mapping = {
    0: 'CN-CN',
    1: 'CN-MCI',
    2: 'MCI-MCI',
    3: 'MCI-AD',
    4: 'AD-AD'
}

predictions = [reverse_mapping[pred] for pred in predictions]
predictions

NameError: name 'xgb_model' is not defined

In [30]:
data = pd.DataFrame({
    'RowId': np.arange(1, len(predictions) + 1), 
    'Result': predictions
})

data.to_csv('LR_RFE_top100features.csv', index=False)